In [14]:
import pandas as pd
import plotly.graph_objects as go

In [15]:
# --- USER SETTINGS ---
h_out_default = 5.0  # W/m²·K

In [16]:
weather_df = pd.read_csv("data-collection/weather_2021.csv")
weather_df["timestamp"] = pd.to_datetime(weather_df["timestamp"])
weather_df.set_index("timestamp", inplace=True)

In [17]:
# --- 1. Read box configurations ---
df_cfg = pd.read_csv("data-collection/box_insulated_thermal_time_constants.csv")
df_cfg["C_total (J/K)"] = df_cfg["C_total (J/K)"].astype(float)
df_cfg["R_total (K/W)"] = df_cfg["R_total (K/W)"].astype(float)

# --- 2. Simulation function ---
def simulate_box(T_out_series, C, R_total, dt=3600):
    T = T_out_series.iloc[0]
    res = []
    for T_out in T_out_series:
        T = T + (dt / (C * R_total)) * (T_out - T)
        res.append(T)
    return pd.Series(res, index=T_out_series.index)  # keep datetime index

# --- 3. Create Plotly figure ---
fig = go.Figure()

# Outdoor temperature
fig.add_trace(go.Scatter(
    x=weather_df.index,
    y=weather_df["T_out"],
    mode="lines",
    name="Outdoor Temp",
    opacity=0.5,
    line=dict(color='gray')
))

# Simulate each box configuration
for _, row in df_cfg.iterrows():
    C = row["C_total (J/K)"]
    R = row["R_total (K/W)"]
    series = simulate_box(weather_df["T_out"], C, R)
    series = series.astype(float).ffill()  # forward-fill missing values
    label = f"{int(row.get('insulation (mm)',0))} mm, {row.get('water (L)',0)} L, h={row.get('h_out (W/m2K)', h_out_default)}"
    
    fig.add_trace(go.Scatter(
        x=series.index,
        y=series.values,
        mode='lines',
        name=label,
        opacity=0.7,
        connectgaps=False,
        visible='legendonly'
    ))

# Layout
fig.update_layout(
    title="Box Temperature Simulations (2021 Outdoor Temps)",
    xaxis_title="Date",
    yaxis_title="Temperature (°C)",
    xaxis=dict(
        showgrid=True,
        tickformat="%b %d",  # Month Day format
        nticks=12
    ),
    legend=dict(title="Box Configurations"),
    template="plotly_white",
    width=1200,
    height=600
)

fig.show()
